In [1]:
import pyproj
import math
from pykalman import KalmanFilter
import numpy as np
import plotly.express as px 
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from utils import  read_keyframe_trajectory, read_map_points, kabsch_umeyama, smooth_elevation


keyframes = read_keyframe_trajectory("KeyframeTrajectory.txt", "GPSTrajectory.txt")[1:] # skip first keyframe (0,0,0)
map_points = read_map_points("MapPoints.txt")

In [2]:
# Plot SLAM trajectory and map points

kf_trajectory = np.array([ [kf.x, kf.y, kf.z] for kf in keyframes])
mp_points = np.array([ [mp.x, mp.y, mp.z] for mp in map_points])

slam_fig = go.Figure(data=[go.Scatter3d(x=kf_trajectory[:, 0], y=kf_trajectory[:, 1], z=kf_trajectory[:, 2], mode='lines'),
                           go.Scatter3d(x=mp_points[:, 0], y=mp_points[:, 1], z=mp_points[:, 2], mode='markers', marker=dict(size=0.5, opacity=0.5))],
                layout=dict(height=500, width=800, margin=dict(l=0, r=0, b=0, t=10)))
slam_fig.show()

#

In [3]:
# 2. Transform GPS (lat,lon) coordinates to Mercator (x,y) coordinates
tr = pyproj.Transformer.from_crs("epsg:4326", "epsg:3857", always_xy=True)
scale_factor = 1 / math.cos(math.radians(np.mean([kf.gps.lon for kf in keyframes])))
gps_path = np.array([tr.transform(kf.gps.lon, kf.gps.lat) for kf in keyframes])
elevation = np.array([kf.gps.alt for kf in keyframes])


# comp_fig = make_subplots(rows=1, cols=2)
# comp_fig.add_trace(go.Scatter(x=kf_trajectory[:, 0], y=kf_trajectory[:, 1], mode='lines'), row=1, col=1)
# comp_fig.add_trace(go.Scatter(x=gps_trajectory[:, 0], y=gps_trajectory[:, 1], mode='lines'), row=1, col=2)

# comp_fig.update_layout(height=600, width=1000, title_text="SLAM vs GPS Trajectory")
# comp_fig.show()

# data = np.array([(kf.timestamp, kf.gps.alt) for kf in keyframes[1:]])

# gps_fig = go.Figure(data=[go.Scatter(x=data[:,0], y=data[:,1], mode='markers')])
# gps_fig.show()

trace = go.Scatter3d(x=gps_path[:,0], y=gps_path[:,1], z=elevation, mode='lines')
# # trace = go.Scatter(x=mercator_points[:,0], y=mercator_points[:,1], mode='lines')
gps_fig = go.Figure(data=[trace])

gps_fig.update_layout(scene = dict(aspectmode='manual', aspectratio=dict(x=1, y=scale_factor, z=1)))
gps_fig.show()


In [4]:
# 3. GPS altitude data is noisy, so we need to smooth it

timestamps = np.array([kf.timestamp for kf in keyframes])
noisy_elevation = np.array([kf.gps.alt for kf in keyframes])
smoothed_elevation, filtered_elevation = smooth_elevation(noisy_elevation)

comp_fig = make_subplots(rows=3, cols=1)
comp_fig.add_trace(go.Scatter(x=timestamps, y=noisy_elevation, mode='lines'), row=1, col=1)
comp_fig.add_trace(go.Scatter(x=timestamps, y=smoothed_elevation, mode='lines'), row=2, col=1)
comp_fig.add_trace(go.Scatter(x=timestamps, y=filtered_elevation, mode='lines'), row=3, col=1)

comp_fig.update_layout(title_text="Noisy data vs smoothed vs filtered elevation data")
comp_fig.show()

In [20]:

# 4. Align SLAM trajectory with GPS trajectory

gps_trajectory = np.hstack((gps_path, smoothed_elevation.reshape(-1, 1)))

R, c, t = kabsch_umeyama(gps_trajectory, kf_trajectory)
adjusted_kf_trajectory = np.array([t + c * R @ p for p in kf_trajectory])

traj_comp_fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'scene'}, {'type': 'scene'}]])
traj_comp_fig.add_trace(go.Scatter3d(x=gps_trajectory[:, 0], y=gps_trajectory[:, 1], z=gps_trajectory[:, 2], mode='lines'), row=1, col=1)
traj_comp_fig.add_trace(go.Scatter3d(x=adjusted_kf_trajectory[:, 0], y=adjusted_kf_trajectory[:, 1], z=adjusted_kf_trajectory[:, 2], mode='lines'), row=1, col=2)
# traj_comp_fig.add_trace(go.Scatter(x=gps_trajectory[:, 0], y=gps_trajectory[:, 1], mode='lines'), row=2, col=1)
# traj_comp_fig.add_trace(go.Scatter(x=adjusted_kf_trajectory[:, 0], y=adjusted_kf_trajectory[:, 1], mode='lines'), row=2, col=2)

traj_comp_fig.show()



In [31]:
traj_comp_fig_2d = make_subplots(rows=1, cols=2)
traj_comp_fig_2d.add_trace(go.Scatter(x=gps_trajectory[:, 0], y=gps_trajectory[:, 1], mode='lines'), row=1, col=1)
traj_comp_fig_2d.add_trace(go.Scatter(x=adjusted_kf_trajectory[:, 0], y=adjusted_kf_trajectory[:, 1], mode='lines'), row=1, col=2)
traj_comp_fig_2d.update_yaxes(
    col=1,
    scaleanchor="x",
    scaleratio=scale_factor,
)
traj_comp_fig_2d.update_yaxes(
    col=2,
    scaleanchor="x2",
    scaleratio=scale_factor,
)
traj_comp_fig_2d.show()


In [39]:
# 5. Align map points with adjusted SLAM trajectory

adjusted_mp_points = np.array([t + c * R @ p for p in mp_points])

adjusted_slam_fig = go.Figure(data=[
    go.Scatter3d(x=gps_trajectory[:, 0], y=gps_trajectory[:, 1],z=gps_trajectory[:, 2], mode='lines', name='GPS trajectory'),
    go.Scatter3d(x=adjusted_kf_trajectory[:, 0], y=adjusted_kf_trajectory[:, 1], z=adjusted_kf_trajectory[:, 2], mode='lines', name='adjusted SLAM trajectory'),
    go.Scatter3d(x=adjusted_mp_points[:, 0], y=adjusted_mp_points[:, 1], z=adjusted_mp_points[:, 2], mode='markers', name='adjusted MapPoints', marker=dict(size=0.5, opacity=0.7))],
    layout=dict(height=800, width=1000))
adjusted_slam_fig.show()
